# Vortex Solver

In [1]:
%pylab inline
import cupy as cp
import h5py
import copy
import numpy as np
import json

Populating the interactive namespace from numpy and matplotlib


### Equations

In [2]:
### Padded
def Dx(u,delta):
  d = cp.zeros_like(u)
  d[1:-1,:,:] += (u[2:,:,:] - u[:-2,:,:])/(2*delta)
  d[0,:,:] += (u[1,:,:] - u[0,:,:])/(2*delta)
  d[-1,:,:] += (u[-1,:,:] - u[-2,:,:])/(2*delta)
  return d

def Dy(u,delta):
  d = cp.zeros_like(u)
  d[:,1:-1,:] += (u[:,2:,:] - u[:,:-2,:])/(2*delta)
  d[:,0,:] += (u[:,1,:] - u[:,0,:])/(2*delta)
  d[:,-1,:] += (u[:,-1,:] - u[:,-2,:])/(2*delta)
  return d

def Dz(u,delta):
  d = cp.zeros_like(u)
  d[:,:,1:-1] += (u[:,:,2:] - u[:,:,:-2])/(2*delta)
  d[:,:,0] += (u[:,:,1] - u[:,:,0])/(2*delta)
  d[:,:,-1] += (u[:,:,-1] - u[:,:,-2])/(2*delta)
  return d


def Lap(u,delta):
  d = cp.zeros_like(u)
  d[1:-1,:,:] += (u[2:,:,:] -2*u[1:-1,:,:] + u[:-2,:,:])
  d[0,:,:]    += u[1,:,:] -2*u[0,:,:] + u[0,:,:]#u[2,:,:] -2*u[1,:,:] + u[0,:,:]
  d[-1,:,:]   += u[-1,:,:] -2*u[-1,:,:] + u[-2,:,:]#u[-3,:,:] -2*u[-2,:,:] + u[-1,:,:]

  d[:,1:-1,:] += (u[:,2:,:] -2*u[:,1:-1,:] + u[:,:-2,:])
  d[:,0,:]    += u[:,1,:] -2*u[:,0,:] + u[:,0,:]#u[:,2,:] -2*u[:,1,:] + u[:,0,:]
  d[:,-1,:]   += u[:,-1,:] -2*u[:,-1,:] + u[:,-2,:]#u[:,-3,:] -2*u[:,-2,:] + u[:,-1,:]
    
  d[:,:,1:-1] += (u[:,:,2:] -2*u[:,:,1:-1] + u[:,:,:-2])
  d[:,:,0]    += u[:,:,1] -2*u[:,:,0] + u[:,:,0]#u[:,:,2] -2*u[:,:,1] + u[:,:,0]
  d[:,:,-1]   += u[:,:,-1] -2*u[:,:,-1] + u[:,:,-2]#u[:,:,-3] -2*u[:,:,-2] + u[:,:,-1]

  d[:,:,:] *= 1/delta**2

  return d

 
def EOM(fields,delta,lam,Q,V,omega):

    
    ## Dxyz Phis
    dx_phir  = Dx(fields[0],delta)
    dy_phir  = Dy(fields[0],delta)
    dz_phir  = Dz(fields[0],delta)
    
    dx_phii  = Dx(fields[1],delta)
    dy_phii  = Dy(fields[1],delta)
    dz_phii  = Dz(fields[1],delta)
    
    ## Fields
    phi_r= fields[0]
    phi_i= fields[1]
    chi1 = fields[2]
    chi2 = fields[3]
    chi3 = fields[4]
    Ax   = fields[5]
    Ay   = fields[6]
    Az   = fields[7]
    At   = fields[8]
    
    ### OLD version

    mod_phi = 2*lam*(phi_r**2 + phi_i**2)
    mod_chi = 2*lam*(chi1**2 +chi2**2 +chi3**2 -V**2)
    mod_A   = Q**2*(Ax**2 + Ay**2 + Az**2 - At**2)    
    
    mod_chi += mod_phi
    mod_A   += mod_chi
    
    
    #####################
    #####################
    ####### higgs #######
    
    ## aux calcs
    
    AmuDmuphi_r = Ax*dx_phir
    AmuDmuphi_r += Ay*dy_phir
    AmuDmuphi_r += Az*dz_phir
    AmuDmuphi_r -= At*fields[9]
    AmuDmuphi_r *= 2*Q
    
    AmuDmuphi_i = Ax*dx_phii
    AmuDmuphi_i += Ay*dy_phii
    AmuDmuphi_i += Az*dz_phii
    AmuDmuphi_i -= At*fields[10]
    AmuDmuphi_i *= 2*Q
    
    ## Eqs
    
    lap = Lap(phi_r,delta)
    eq1 = lap - mod_A*phi_r - AmuDmuphi_i
    
    lap[:,:,:] = Lap(phi_i,delta)
    eq2 = lap - mod_A*phi_i + AmuDmuphi_r

    #####################
    #####################
    ####### chis ########
    
    mod_chi += omega**2
    
    lap[:,:,:] = Lap(chi1,delta)
    eq3     = lap - mod_chi*chi1
    
    lap[:,:,:] = Lap(chi2,delta)
    eq4     = lap - mod_chi*chi2
    
    lap[:,:,:]  = Lap(chi3,delta)
    eq5     = lap -mod_chi*chi3

    
    #####################
    #####################
    ####### As ##########
    
    ### aux calc
    mod_phi *= 1/lam * Q**2
    
    dx_phir *= phi_i
    dx_phir -= dx_phii*phi_r
    dx_phir *= 2*Q
    
    dy_phir *= phi_i
    dy_phir -= dy_phii*phi_r
    dy_phir *= 2*Q

    dz_phir *= phi_i
    dz_phir -= dz_phii*phi_r
    dz_phir *= 2*Q

    #### eqs
    lap[:,:,:] = Lap(Ax,delta)
    eq6 = lap - Ax*mod_phi + dx_phir
    
    lap[:,:,:] = Lap(Ay,delta)
    eq7 = lap - Ay*mod_phi + dy_phir
    
    lap[:,:,:] = Lap(Az,delta)
    eq8 = lap - Az*mod_phi + dz_phir
    
    lap[:,:,:] = Lap(At,delta)
    eq9 = lap - At*mod_phi + 2*Q* (phi_i*fields[9] - phi_r*fields[10] )
    
    
    return cp.array([fields[9],fields[10],fields[11],fields[12],fields[13],fields[14],fields[15],fields[16],fields[17],eq1,eq2,eq3,eq4,eq5,eq6,eq7,eq8,eq9])
    


In [3]:
def Tmunu(fields,delta,lam,Q,V,omega,L):
    
    aux = cp.linspace(-L/2,L/2,len(fields[0][0,0,:]))
    x = np.tile(aux,(len(aux),len(aux),1))
    y = np.zeros_like(x)
    z = np.zeros_like(x)
    for i in range(len(aux)):
        y[:,i,:] += x[:,:,i]
    for i in range(len(aux)):
        z[i,:,:] += x[:,:,i]
    ### matter
    #################
    
    phi_r= fields[0]
    phi_i= fields[1]
    chi1 = fields[2]
    chi2 = fields[3]
    chi3 = fields[4]
    Ax   = fields[5]
    Ay   = fields[6]
    Az   = fields[7]
    A0   = fields[8]

     
    ### moments fields
    #################
    dt_phir = fields[9]
    dt_phii = fields[10]
    dt_chi1 = fields[11]
    dt_chi2 = fields[12]
    dt_chi3 = fields[13]
    dt_Ax   = fields[14]
    dt_Ay   = fields[15]
    dt_Az   = fields[16]
    dt_At   = fields[17]


    
    ### Spatial derivatives
    dx_phir  = Dx(fields[0],delta)
    dy_phir  = Dy(fields[0],delta)
    dz_phir  = Dz(fields[0],delta)
    
    dx_phii  = Dx(fields[1],delta)
    dy_phii  = Dy(fields[1],delta)
    dz_phii  = Dz(fields[1],delta)
    
    dx_chi1 =  Dx(fields[2],delta)
    dy_chi1 =  Dy(fields[2],delta)
    dz_chi1 =  Dz(fields[2],delta)
    
    dx_chi2 =  Dx(fields[3],delta)
    dy_chi2 =  Dy(fields[3],delta)
    dz_chi2 =  Dz(fields[3],delta)
    
    dx_chi3 =  Dx(fields[4],delta)
    dy_chi3 =  Dy(fields[4],delta)
    dz_chi3 =  Dz(fields[4],delta)
    
    dx_Ax   =  Dx(fields[5],delta)
    dy_Ax   =  Dy(fields[5],delta)
    dz_Ax   =  Dz(fields[5],delta)
    
    dx_Ay   =  Dx(fields[6],delta)
    dy_Ay   =  Dy(fields[6],delta)
    dz_Ay   =  Dz(fields[6],delta)
    
    dx_Az   =  Dx(fields[7],delta)
    dy_Az   =  Dy(fields[7],delta)
    dz_Az   =  Dz(fields[7],delta)
    
    dx_A0   =  Dx(fields[8],delta)
    dy_A0   =  Dy(fields[8],delta)
    dz_A0   =  Dz(fields[8],delta)
    
    T00 = (((dt_chi1**2 + dt_chi2**2 + dt_chi3**2 + dt_phii**2 + dt_phir**2 +\
             1/2 *(dt_Ax - dx_A0)**2 + dx_chi1**2 + dx_chi2**2 + dx_chi3**2 + dx_phii**2 +\
             dx_phir**2 + 1/2* (dt_Ay - dy_A0)**2 + 1/2* (dx_Ay - dy_Ax)**2 +\
             dy_chi1**2 + dy_chi2**2 + dy_chi3**2 + dy_phii**2 + dy_phir**2 +\
             1/2* (dt_Az - dz_A0)**2 + 1/2* (dx_Az - dz_Ax)**2 + 1/2* (dy_Az - dz_Ay)**2 +\
             dz_chi1**2 + dz_chi2**2 + dz_chi3**2 + dz_phii**2 + dz_phir**2 +\
             2 *(A0* dt_phir + Ax *dx_phir + Ay* dy_phir + Az* dz_phir)* phi_i *Q -\
             2 *(A0* dt_phii + Ax *dx_phii + Ay* dy_phii +\
             Az *dz_phii)* phi_r* Q + (A0**2 + Ax**2 + Ay**2 + Az**2)* (phi_i**2 +\
                                                                        phi_r**2)* Q**2))) + ((((chi1**2 + chi2**2 + chi3**2) *omega**2 +\
            lam *(chi1**2 + chi2**2 + chi3**2 + phi_i**2 + phi_r**2 - V**2)**2)))


    L1 = z* (dt_Ax* (dx_Ay - dy_Ax) + dx_A0* (-dx_Ay + dy_Ax) - dt_Az *dy_Az -\
    2* dt_chi1* dy_chi1 - 2* dt_chi2* dy_chi2 - 2* dt_chi3 *dy_chi3 -\
    2 *dt_phii* dy_phii - 2* dt_phir* dy_phir + dy_Az* dz_A0 +\
    dt_Az* dz_Ay - dz_A0* dz_Ay - 2* Ay* Q* dt_phir* phi_i -\
    2 *A0* Q* dy_phir *phi_i - 2* A0 *Ay* Q**2 *phi_i**2 +\
    2 *Ay* Q* dt_phii* phi_r + 2* A0 *Q* dy_phii* phi_r -\
    2* A0* Ay* Q**2 *phi_r**2) -\
    y*(dt_Ay* dy_Az - dy_A0* dy_Az + dt_Ax* (dx_Az - dz_Ax) +\
    dx_A0* (-dx_Az + dz_Ax) - dt_Ay* dz_Ay + dy_A0 *dz_Ay -\
    2 *dt_chi1* dz_chi1 - 2 *dt_chi2* dz_chi2 - 2 *dt_chi3* dz_chi3 -\
    2* dt_phii* dz_phii - 2 *dt_phir* dz_phir - 2* Az* Q* dt_phir* phi_i -\
    2* A0* Q *dz_phir* phi_i - 2* A0* Az* Q**2* phi_i**2 +\
    2 *Az* Q* dt_phii* phi_r + 2* A0 *Q* dz_phii* phi_r - 2 *A0 *Az* Q**2* phi_r**2)

   
    L2 = z* (2 *dt_chi1* dx_chi1 + 2* dt_chi2* dx_chi2 + 2* dt_chi3* dx_chi3 +\
    2* dt_phii* dx_phii + 2* dt_phir* dx_phir - dx_Ay*dy_A0 +\
    dt_Ay *(dx_Ay - dy_Ax) + dy_A0 *dy_Ax - dx_Az* dz_A0 +\
    dt_Az *(dx_Az - dz_Ax) + dz_A0 *dz_Ax + 2* Ax* Q* dt_phir* phi_i +\
    2* A0* Q* dx_phir* phi_i + 2* A0 *Ax* Q**2 *phi_i**2 -\
    2* Ax* Q *dt_phii* phi_r - 2* A0* Q* dx_phii* phi_r +\
    2* A0 *Ax* Q**2* phi_r**2) +\
    x* (dt_Ay* dy_Az - dy_A0* dy_Az + dt_Ax* (dx_Az - dz_Ax) +\
    dx_A0* (-dx_Az + dz_Ax) - dt_Ay* dz_Ay + dy_A0* dz_Ay -\
    2* dt_chi1* dz_chi1 - 2 *dt_chi2* dz_chi2 - 2* dt_chi3 *dz_chi3 -\
    2* dt_phii* dz_phii - 2* dt_phir*dz_phir - 2* Az* Q* dt_phir* phi_i -\
    2* A0* Q* dz_phir* phi_i - 2* A0 *Az* Q**2* phi_i**2 +\
    2 *Az* Q* dt_phii* phi_r + 2* A0* Q* dz_phii* phi_r - 2* A0* Az* Q**2* phi_r**2)
    
    L3 =-y* (2 *dt_chi1 *dx_chi1 + 2* dt_chi2* dx_chi2* + 2* dt_chi3 *dx_chi3 +\
    2* dt_phii* dx_phii + 2* dt_phir* dx_phir - dx_Ay* dy_A0 +\
    dt_Ay* (dx_Ay - dy_Ax) + dy_A0 *dy_Ax - dx_Az* dz_A0 +\
    dt_Az* (dx_Az - dz_Ax) + dz_A0* dz_Ax + 2* Ax* Q* dt_phir* phi_i +\
    2* A0* Q* dx_phir* phi_i + 2* A0* Ax* Q**2* phi_i**2 -\
    2* Ax* Q* dt_phii* phi_r - 2* A0* Q* dx_phii* phi_r +\
    2* A0* Ax* Q**2 *phi_r**2) +\
    x* (dx_A0* (dx_Ay - dy_Ax) + dt_Ax* (-dx_Ay + dy_Ax) + dt_Az* dy_Az +\
    2* dt_chi1* dy_chi1 + 2* dt_chi2* dy_chi2 + 2* dt_chi3 *dy_chi3 +\
    2* dt_phii* dy_phii + 2* dt_phir* dy_phir - dy_Az* dz_A0 -\
    dt_Az* dz_Ay + dz_A0* dz_Ay + 2* Ay* Q* dt_phir* phi_i +\
    2* A0* Q* dy_phir* phi_i + 2* A0* Ay* Q**2 *phi_i**2 -\
    2* Ay* Q* dt_phii* phi_r - 2* A0* Q* dy_phii* phi_r + 2 *A0* Ay* Q**2 *phi_r**2)
    
    return cp.array([T00 ,cp.sqrt(L1**2+L2**2+L3**2)])

## Rk4

In [4]:
def OneStep(fields,dt,k):
  out = fields + k*dt
  return out 

def RK4step(fields,delta,dt,lam,Q,V,omega):
  #k = EqDif(fields,delta,lam,Q,V,omega) ## k1
  k = EOM(fields,delta,lam,Q,V,omega) ## k1

  f_aux = OneStep(fields,dt/2,k) ## u1 = u +dt/2*k1

  #k_aux = EqDif(f_aux,delta,lam,Q,V,omega) ## k2
  k_aux = EOM(f_aux,delta,lam,Q,V,omega) ## k2
  k[:,:,:,:] += 2*k_aux ## armo el ultimo k

  f_aux[:,:,:,:] = OneStep(fields,dt/2,k_aux) ## u2
  #k_aux[:,:,:,:] = EqDif(f_aux,delta,lam,Q,V,omega) ## k3
  k_aux[:,:,:,:] = EOM(f_aux,delta,lam,Q,V,omega) ## k3

  k[:,:,:,:] += 2*k_aux ## armo el ultimo k
  f_aux[:,:,:,:] = OneStep(fields,dt,k_aux) ## u3

  #k_aux[:,:,:,:] = EqDif(f_aux,delta,lam,Q,V,omega) ## k4 
  k_aux[:,:,:,:] = EOM(f_aux,delta,lam,Q,V,omega) ## k4 
  k[:,:,:,:] += k_aux 
  f_aux[:,:,:,:] = OneStep(fields,dt/6,k) ## new u

  return f_aux

# SIMULATION

### Pars

In [5]:
def name2process(path,name):
    return rename(path+name,path+name[:-3] +'_processing.h5' )
def name2done(path,name):
    return rename(path+name[:-3] +'_processing.h5',path+name[:-3] +'_done.h5' )


In [6]:
def leadSeed(path,name,continuation = False):
    if continuation:
        with h5py.File(path+name, 'r') as f:
            # List all groups
            #print("Keys: %s" % f.keys())
            a_group_key = list(f.keys())[0]
            with cp.cuda.Device(0):
                data0 = cp.array(f[a_group_key]["fields"])
    else:
        with h5py.File(path+name, 'r') as f:
            a_group_key = list(f.keys())[0]
            with cp.cuda.Device(0):
                data0 = cp.array(f[a_group_key])
    return data0
        

In [7]:
def SimulationRun(all_fields0,pars0,hkeys,hValues0,simul_path,seed_path,name,skip = 1):
    N0,delta0,dt0,lam0,Q0,V0,omega0 = pars0

    N = N0
    ## sim GPU0
    hf0 = h5py.File(simul_path+"simul_py" +name[:-3]+"_fields.h5", 'w')
    hf1 = h5py.File(simul_path+"simul_py" +name[:-3]+"_T.h5", 'w')
    hf2 = h5py.File(seed_path+"seed{}_".format(int(130+N)) +name[:-3]+".h5", 'w')

    for k,Val in zip(hkeys,hValues0):
        hf0.attrs[k] = Val
        hf2.attrs[k] = Val

    i = 0
    while i <= N:
        with cp.cuda.Device(0):
            all_fields0[:,:,:,:] = RK4step(all_fields0,delta0,dt0,lam0,Q0,V0,omega0)
            if i in snap_list:
            ### GUARDO FIELDS 0
                fields = cp.asnumpy(all_fields0)
                string_name = '0'*(10-len(str(i))) + str(i)
                grp_fields = hf0.create_group(string_name)
                Dus = grp_fields.create_dataset("Du", data = [f[::skip,::skip,::skip] for f in fields[9:]])
                us = grp_fields.create_dataset("u", data = [f[::skip,::skip,::skip] for f in fields[:9]] )
                
                grp_T = hf1.create_group(string_name)
                T_L = cp.asnumpy(Tmunu(all_fields0,delta0,lam0,Q0,V0,omega0,hValues0[7]))
                grp_T.create_dataset("T", data =[t[::skip,::skip,::skip] for t in T_L])
            if i == N:
                grp_seed =  hf2.create_group("fields")
                fs = grp_seed.create_dataset("fields", data = fields)
        i +=1
        print(i)
    hf0.close()
    hf1.close()
    hf2.close()
    return



In [8]:
from os import listdir
from os.path import isfile, join
from os import rename
import time

#squareseed51try_v6sep2lX140nocurrents
#mypath = "F:\Vortex_simulations\seedssquare\square\\"
#seed2_path = "F:\Vortex_simulations\seedssquare\seeds_post130\\"
#simul_path = "F:\\Vortex_simulations\\simulsquares\\"

seed_path = "G:\\seedswithdifferentL\\case3\\"

simul_path ="G:\\simulswithdifferentL\\case 3\\"
#onlyfiles = [f for f in listdir(seeds_path) if isfile(join(seeds_path, f))]

#print(listdir(seeds_path))

In [9]:
onlyfiles = [f for f in listdir(seed_path) if isfile(join(seed_path, f))]
seed_files = list(filter(lambda x: "h5" in x,onlyfiles))
parameters_files = list(filter(lambda x: "parameters" in x,onlyfiles))


In [10]:
print(onlyfiles)

['parametersseed1.json', 'parametersseed2.json', 'parametersseed3.json', 'parametersseed4.json', 'parametersseed5.json', 'parametersseed6.json', 'parametersseed7.json', 'parametersseed8.json', 'seed120130_seed1.h5', 'seed120130_seed2.h5', 'seed120130_seed3.h5', 'seed1_done.h5', 'seed2_done.h5', 'seed3_processing.h5', 'seed4.h5', 'seed5.h5', 'seed6.h5', 'seed7.h5', 'seed8.h5']


In [ ]:
#while True:
#onlyfiles = [f for f in listdir(mypath) if isfile(join(mypath, f))]
for file in onlyfiles:# ["seedtry.h5"]:
    if "processing" not in file and "done" not in file and ".json" not in file and "130" not in file:
                
        #try:
        all_fields = leadSeed(seed_path,file)
        
        ### new parameters ###
        number = file.split(".")[0][-1]
        
        path_pars = "G:\\seedswithdifferentL\\case3\\parametersseed{}.json".format(number)
        with open(path_pars,"rb") as f:
            pars_json = json.load(f)
        
        
        L0 = pars_json["lX"]#181.782
        Nx = pars_json["nX"]#351
        delta = pars_json["delta"]
        ### PARS0
        delta0 = delta #0.333024
        dt0 = 0.001
        Q0 = 0.21213203435596423
        lam0 = 0.25
        V0 = 5.
        omega0 = 0.25
        N0 = 120000
        pars0 = [N0,delta0,dt0,lam0,Q0,V0,omega0]
        
        hkeys = ['checkpointInterval','dt',  'kerOrderX','kerOrderY', 'kerOrderZ','lR', 'lX', 'lY','lZ','nR','nX','nY','nZ','q','rA','rχ','rϕ','v', 'λ', 'χ0', 'ω', 'ϵ']
        
        hvalues0 = [500,dt0,2,2,2,np.sqrt(2)*100,L0,L0,L0,12001,Nx,Nx,Nx,Q0,1.34241,2.33117,0.799732,V0,lam0,4.79612,omega0,10e-5]

        snap_list = np.arange(0,N0+1,500)

        
        ######### run
        print("Im runnin'", file)
        name2process(seed_path,file)
      
        
        SimulationRun(all_fields,pars0,hkeys,hvalues0,simul_path,seed_path,file,skip = 1)

        name2done(seed_path,file)
        all_fields = None
        print("done with",file)
    #except:
        #    continue
    else:
        continue
    #time.sleep(1800)

        

            
            

Im runnin' seed4.h5
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272


1857
1858
1859
1860
1861
1862
1863
1864
1865
1866
1867
1868
1869
1870
1871
1872
1873
1874
1875
1876
1877
1878
1879
1880
1881
1882
1883
1884
1885
1886
1887
1888
1889
1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056


3496
3497
3498
3499
3500
3501
3502
3503
3504
3505
3506
3507
3508
3509
3510
3511
3512
3513
3514
3515
3516
3517
3518
3519
3520
3521
3522
3523
3524
3525
3526
3527
3528
3529
3530
3531
3532
3533
3534
3535
3536
3537
3538
3539
3540
3541
3542
3543
3544
3545
3546
3547
3548
3549
3550
3551
3552
3553
3554
3555
3556
3557
3558
3559
3560
3561
3562
3563
3564
3565
3566
3567
3568
3569
3570
3571
3572
3573
3574
3575
3576
3577
3578
3579
3580
3581
3582
3583
3584
3585
3586
3587
3588
3589
3590
3591
3592
3593
3594
3595
3596
3597
3598
3599
3600
3601
3602
3603
3604
3605
3606
3607
3608
3609
3610
3611
3612
3613
3614
3615
3616
3617
3618
3619
3620
3621
3622
3623
3624
3625
3626
3627
3628
3629
3630
3631
3632
3633
3634
3635
3636
3637
3638
3639
3640
3641
3642
3643
3644
3645
3646
3647
3648
3649
3650
3651
3652
3653
3654
3655
3656
3657
3658
3659
3660
3661
3662
3663
3664
3665
3666
3667
3668
3669
3670
3671
3672
3673
3674
3675
3676
3677
3678
3679
3680
3681
3682
3683
3684
3685
3686
3687
3688
3689
3690
3691
3692
3693
3694
3695


5135
5136
5137
5138
5139
5140
5141
5142
5143
5144
5145
5146
5147
5148
5149
5150
5151
5152
5153
5154
5155
5156
5157
5158
5159
5160
5161
5162
5163
5164
5165
5166
5167
5168
5169
5170
5171
5172
5173
5174
5175
5176
5177
5178
5179
5180
5181
5182
5183
5184
5185
5186
5187
5188
5189
5190
5191
5192
5193
5194
5195
5196
5197
5198
5199
5200
5201
5202
5203
5204
5205
5206
5207
5208
5209
5210
5211
5212
5213
5214
5215
5216
5217
5218
5219
5220
5221
5222
5223
5224
5225
5226
5227
5228
5229
5230
5231
5232
5233
5234
5235
5236
5237
5238
5239
5240
5241
5242
5243
5244
5245
5246
5247
5248
5249
5250
5251
5252
5253
5254
5255
5256
5257
5258
5259
5260
5261
5262
5263
5264
5265
5266
5267
5268
5269
5270
5271
5272
5273
5274
5275
5276
5277
5278
5279
5280
5281
5282
5283
5284
5285
5286
5287
5288
5289
5290
5291
5292
5293
5294
5295
5296
5297
5298
5299
5300
5301
5302
5303
5304
5305
5306
5307
5308
5309
5310
5311
5312
5313
5314
5315
5316
5317
5318
5319
5320
5321
5322
5323
5324
5325
5326
5327
5328
5329
5330
5331
5332
5333
5334


6774
6775
6776
6777
6778
6779
6780
6781
6782
6783
6784
6785
6786
6787
6788
6789
6790
6791
6792
6793
6794
6795
6796
6797
6798
6799
6800
6801
6802
6803
6804
6805
6806
6807
6808
6809
6810
6811
6812
6813
6814
6815
6816
6817
6818
6819
6820
6821
6822
6823
6824
6825
6826
6827
6828
6829
6830
6831
6832
6833
6834
6835
6836
6837
6838
6839
6840
6841
6842
6843
6844
6845
6846
6847
6848
6849
6850
6851
6852
6853
6854
6855
6856
6857
6858
6859
6860
6861
6862
6863
6864
6865
6866
6867
6868
6869
6870
6871
6872
6873
6874
6875
6876
6877
6878
6879
6880
6881
6882
6883
6884
6885
6886
6887
6888
6889
6890
6891
6892
6893
6894
6895
6896
6897
6898
6899
6900
6901
6902
6903
6904
6905
6906
6907
6908
6909
6910
6911
6912
6913
6914
6915
6916
6917
6918
6919
6920
6921
6922
6923
6924
6925
6926
6927
6928
6929
6930
6931
6932
6933
6934
6935
6936
6937
6938
6939
6940
6941
6942
6943
6944
6945
6946
6947
6948
6949
6950
6951
6952
6953
6954
6955
6956
6957
6958
6959
6960
6961
6962
6963
6964
6965
6966
6967
6968
6969
6970
6971
6972
6973


...

14141
14142
14143
14144
14145
14146
14147
14148
14149
14150
14151
14152
14153
14154
14155
14156
14157
14158
14159
14160
14161
14162
14163
14164
14165
14166
14167
14168
14169
14170
14171
14172
14173
14174
14175
14176
14177
14178
14179
14180
14181
14182
14183
14184
14185
14186
14187
14188
14189
14190
14191
14192
14193
14194
14195
14196
14197
14198
14199
14200
14201
14202
14203
14204
14205
14206
14207
14208
14209
14210
14211
14212
14213
14214
14215
14216
14217
14218
14219
14220
14221
14222
14223
14224
14225
14226
14227
14228
14229
14230
14231
14232
14233
14234
14235
14236
14237
14238
14239
14240
14241
14242
14243
14244
14245
14246
14247
14248
14249
14250
14251
14252
14253
14254
14255
14256
14257
14258
14259
14260
14261
14262
14263
14264
14265
14266
14267
14268
14269
14270
14271
14272
14273
14274
14275
14276
14277
14278
14279
14280
14281
14282
14283
14284
14285
14286
14287
14288
14289
14290
14291
14292
14293
14294
14295
14296
14297
14298
14299
14300
14301
14302
14303
14304
14305
14306
1430

15507
15508
15509
15510
15511
15512
15513
15514
15515
15516
15517
15518
15519
15520
15521
15522
15523
15524
15525
15526
15527
15528
15529
15530
15531
15532
15533
15534
15535
15536
15537
15538
15539
15540
15541
15542
15543
15544
15545
15546
15547
15548
15549
15550
15551
15552
15553
15554
15555
15556
15557
15558
15559
15560
15561
15562
15563
15564
15565
15566
15567
15568
15569
15570
15571
15572
15573
15574
15575
15576
15577
15578
15579
15580
15581
15582
15583
15584
15585
15586
15587
15588
15589
15590
15591
15592
15593
15594
15595
15596
15597
15598
15599
15600
15601
15602
15603
15604
15605
15606
15607
15608
15609
15610
15611
15612
15613
15614
15615
15616
15617
15618
15619
15620
15621
15622
15623
15624
15625
15626
15627
15628
15629
15630
15631
15632
15633
15634
15635
15636
15637
15638
15639
15640
15641
15642
15643
15644
15645
15646
15647
15648
15649
15650
15651
15652
15653
15654
15655
15656
15657
15658
15659
15660
15661
15662
15663
15664
15665
15666
15667
15668
15669
15670
15671
15672
1567

16873
16874
16875
16876
16877
16878
16879
16880
16881
16882
16883
16884
16885
16886
16887
16888
16889
16890
16891
16892
16893
16894
16895
16896
16897
16898
16899
16900
16901
16902
16903
16904
16905
16906
16907
16908
16909
16910
16911
16912
16913
16914
16915
16916
16917
16918
16919
16920
16921
16922
16923
16924
16925
16926
16927
16928
16929
16930
16931
16932
16933
16934
16935
16936
16937
16938
16939
16940
16941
16942
16943
16944
16945
16946
16947
16948
16949
16950
16951
16952
16953
16954
16955
16956
16957
16958
16959
16960
16961
16962
16963
16964
16965
16966
16967
16968
16969
16970
16971
16972
16973
16974
16975
16976
16977
16978
16979
16980
16981
16982
16983
16984
16985
16986
16987
16988
16989
16990
16991
16992
16993
16994
16995
16996
16997
16998
16999
17000
17001
17002
17003
17004
17005
17006
17007
17008
17009
17010
17011
17012
17013
17014
17015
17016
17017
17018
17019
17020
17021
17022
17023
17024
17025
17026
17027
17028
17029
17030
17031
17032
17033
17034
17035
17036
17037
17038
1703

18239
18240
18241
18242
18243
18244
18245
18246
18247
18248
18249
18250
18251
18252
18253
18254
18255
18256
18257
18258
18259
18260
18261
18262
18263
18264
18265
18266
18267
18268
18269
18270
18271
18272
18273
18274
18275
18276
18277
18278
18279
18280
18281
18282
18283
18284
18285
18286
18287
18288
18289
18290
18291
18292
18293
18294
18295
18296
18297
18298
18299
18300
18301
18302
18303
18304
18305
18306
18307
18308
18309
18310
18311
18312
18313
18314
18315
18316
18317
18318
18319
18320
18321
18322
18323
18324
18325
18326
18327
18328
18329
18330
18331
18332
18333
18334
18335
18336
18337
18338
18339
18340
18341
18342
18343
18344
18345
18346
18347
18348
18349
18350
18351
18352
18353
18354
18355
18356
18357
18358
18359
18360
18361
18362
18363
18364
18365
18366
18367
18368
18369
18370
18371
18372
18373
18374
18375
18376
18377
18378
18379
18380
18381
18382
18383
18384
18385
18386
18387
18388
18389
18390
18391
18392
18393
18394
18395
18396
18397
18398
18399
18400
18401
18402
18403
18404
1840

19605
19606
19607
19608
19609
19610
19611
19612
19613
19614
19615
19616
19617
19618
19619
19620
19621
19622
19623
19624
19625
19626
19627
19628
19629
19630
19631
19632
19633
19634
19635
19636
19637
19638
19639
19640
19641
19642
19643
19644
19645
19646
19647
19648
19649
19650
19651
19652
19653
19654
19655
19656
19657
19658
19659
19660
19661
19662
19663
19664
19665
19666
19667
19668
19669
19670
19671
19672
19673
19674
19675
19676
19677
19678
19679
19680
19681
19682
19683
19684
19685
19686
19687
19688
19689
19690
19691
19692
19693
19694
19695
19696
19697
19698
19699
19700
19701
19702
19703
19704
19705
19706
19707
19708
19709
19710
19711
19712
19713
19714
19715
19716
19717
19718
19719
19720
19721
19722
19723
19724
19725
19726
19727
19728
19729
19730
19731
19732
19733
19734
19735
19736
19737
19738
19739
19740
19741
19742
19743
19744
19745
19746
19747
19748
19749
19750
19751
19752
19753
19754
19755
19756
19757
19758
19759
19760
19761
19762
19763
19764
19765
19766
19767
19768
19769
19770
1977